# NOTEBOOK IS IN DEVELOPMENT

# Table of contents
1. [Introduction](#introduction)
1. [Install pre-release of CLTK](#install)
1. [Load data](#load)
1. [Run NLP pipeline with `NLP()`](#run-nlp)
1. [Inspect CLTK `Doc`](#inspect-doc)
1. [Inspect CLTK `Word`](#inspect-word)
1. [Modeling morphology with `MorphosyntacticFeature` and `MorphosyntacticFeatureBundle`](#morph)
1. [Modeling syntax with `Form` and `DependencyTree`](#syntax)
1. [Feature extraction](#features)
1. [Brief demonstration of `NLP()` for Ancient Greek](#greek-nlp)

# Introduction <a name="introduction"></a>

This notebook is based on [a notebook](https://github.com/cltk/cltk/blob/master/notebooks/CLTK%20Demonstration.ipynb) from the [Classical Language Toolkit project](http://cltk.org). We will annotate the text of the Vulgate of Genesis, using the pipeline that is provided for the Latin language. We use the text of the Latin Genesis as it is provided [here](https://github.com/cltk/lat_text_tesserae).

This notebook demonstrates how to use `NLP()`, the CLTK's primary interface, in Latin and Ancient Greek. Pipelines are available for 17 languages (see [Languages](https://docs.cltk.org/en/latest/languages.html) in the docs).

Full documentation available at <https://docs.cltk.org/en/latest/cltk.html#cltk.nlp.NLP>.



In [60]:
import pandas as pd

# Install CLTK <a name="install"></a>

In [ ]:
## Requires Python 3.7, 3.8, or 3.9

# !pip install cltk

## Load data <a name="load"></a>

Open the text of Genesis, read it line by line, parse the label (book, chapter, verse), and store the data in the dictionary vulgate_genesis. In this dict, the keys are a tuple containing book, chapter and verse, and the values consist of a string, containing the text of a verse.

In [1]:
vulgate_genesis = {}

with open("jerome.vulgate.part.1.genesis.tess") as gen:
    for line in gen:

        label, text = line.split('> ')
        _, bo_ch_ve = label.split()
        bo, ch, ve = bo_ch_ve.split('.')
        vulgate_genesis[(bo, ch, ve)] = text.strip()


How many verses are there in Genesis?

In [2]:
len(vulgate_genesis)

1531

What is the text of Genesis 10:10?

In [3]:
vulgate_genesis[('Genesis', '10', '10')]

'fuit autem principium regni eius Babylon et Arach et Archad et Chalanne in terra Sennaar;'

# Run NLP pipeline with `NLP()` <a name="run-nlp"></a>

In [4]:
from cltk import NLP

In [5]:
cltk_nlp = NLP(language="lat")

‎𐤀 CLTK version '1.1.1'.
Pipeline for language 'Latin' (ISO: 'lat'): `LatinNormalizeProcess`, `LatinStanzaProcess`, `LatinEmbeddingsProcess`, `StopsProcess`, `LatinLexiconProcess`.


In [6]:
# Removing ``LatinLexiconProcess`` for this demo b/c it is slow (adds ~9 mins total)
cltk_nlp.pipeline.processes.pop(-1)
print(cltk_nlp.pipeline.processes)

[<class 'cltk.alphabet.processes.LatinNormalizeProcess'>, <class 'cltk.dependency.processes.LatinStanzaProcess'>, <class 'cltk.embeddings.processes.LatinEmbeddingsProcess'>, <class 'cltk.stops.processes.StopsProcess'>]


Let's see what the pipeline does with Genesis 1:1.

In [7]:
cltk_doc = cltk_nlp.analyze(text=vulgate_genesis[('Genesis', '1', '1')])

# Inspect CLTK `Doc` <a name="inspect-doc"></a>

The pipeline has created a Doc object of our string:

In [8]:
print(type(cltk_doc))

<class 'cltk.core.data_types.Doc'>


How can we access this Doc object?

In [9]:
print([x for x in dir(cltk_doc) if not x.startswith("__")])

['_get_words_attribute', 'embeddings', 'embeddings_model', 'language', 'lemmata', 'morphosyntactic_features', 'normalized_text', 'pipeline', 'pos', 'raw', 'sentence_embeddings', 'sentences', 'sentences_strings', 'sentences_tokens', 'stanza_doc', 'stems', 'tokens', 'tokens_stops_filtered', 'words']


Show the tokens! Note that the semicolon at the end is parsed as a separate token.

In [10]:
print(cltk_doc.tokens)

['in', 'principio', 'creavit', 'Deus', 'caelum', 'et', 'terram', ';']


Lemmata.

In [11]:
print(cltk_doc.lemmata)

['in', 'principium', 'creo', 'Deus', 'caelum', 'et', 'terra', ';']


Parts of speech.

In [12]:
print(cltk_doc.pos)

['ADP', 'NOUN', 'VERB', 'PROPN', 'NOUN', 'CCONJ', 'NOUN', 'PUNCT']


sentences_tokens is a list of lists, which contains the sentences in the string under consideration.

In [15]:
print(cltk_doc.sentences_tokens)

[['in', 'principio', 'creavit', 'Deus', 'caelum', 'et', 'terram', ';']]


# Inspect CLTK `Word` <a name="inspect-word"></a>

Most powerful, though, is the ``Doc.words`` accessor, which is a list of ``Word`` objects. These ``Word`` objects contain all information that was generated during the NLP pipeline

In [16]:
# One Word object for each token
print(len(cltk_doc.words))

8


Users can go token-by-token via ``Doc.words`` or via the intermediary step of looping through sentences.

In [17]:
print(cltk_doc.sentences_strings[0])
sentence_gen_1_1 = cltk_doc.sentences[0]  # type: List[Word]

in principio creavit Deus caelum et terram ;


In [34]:
for word in sentence_gen_1_1:
    print(word.features)
    print('')

{AdpositionalType: [preposition]}

{Case: [ablative], Gender: [neuter], Number: [singular]}

{Aspect: [perfective], Mood: [indicative], Number: [singular], Person: [third], Tense: [past], VerbForm: [finite], Voice: [active]}

{Case: [nominative], Gender: [masculine], Number: [singular]}

{Case: [accusative], Gender: [neuter], Number: [singular]}

{}

{Case: [accusative], Gender: [feminine], Number: [singular]}

{}



In this word, you can see information for lexicography (`.lemmata`), semantics (`.embedding`), morphology (`.pos`, `.features`), syntax (`.governor`, `.dependency_relation`), plus other information most users would find helpful (`.stop`, `.named_entity`).

# Modeling morphology with `MorphosyntacticFeature` and `MorphosyntacticFeatureBundle` <a name="morph"></a>

When a language's `Pipeline` builds each `Word` object, morphological information is stored at several accessors. Those of interest to most users are `.pos` and `.features`.

Let's have a look at the verb in the sentence: creavit, which is the third word, so it has index 2.

In [35]:
creav = sentence_gen_1_1[2]
print('Word.string:', creav.string)
print("")

print('Word.pos:', creav.pos)

Word.string: creavit

Word.pos: verb


The CLTK contains classes a specific class for [the annotation types defined by v2 of the Universal Dependencies project](https://universaldependencies.org/u/feat/all.html). In the CLTK's codebase, these are located at [cltk/morphology/universal_dependencies_features.py](https://github.com/cltk/cltk/blob/dev/src/cltk/morphology/universal_dependencies_features.py).

For instance, a Latin verb requires a label for its [https://universaldependencies.org/u/feat/all.html#al-u-feat/Mood](mood) (e.g., indicative), which the UD project defines as "a feature that expresses modality and subclassifies finite verb forms".

Though morphological taggers may annnotate a verb's mood variously ("ind.", "indicative", "Indic", etc.), the CLTK maps the term into the following, standardized `Mood`.

``` python
class Mood(MorphosyntacticFeature):
    """The mood of a verb.
    see https://universaldependencies.org/u/feat/Mood.html
    """

    admirative = auto()
    conditional = auto()
    desiderative = auto()
    imperative = auto()
    indicative = auto()
    jussive = auto()
    necessitative = auto()
    optative = auto()
    potential = auto()
    purposive = auto()
    quotative = auto()
    subjunctive = auto()
```

Turning back to the the above example word, we can see such features at `.features`.

In [36]:
# type
print("type(`Word.features`):", type(creav.features))
print("")
# str repr of `MorphosyntacticFeatureBundle`
print("`Word.features`:", creav.features)

type(`Word.features`): <class 'cltk.morphology.morphosyntax.MorphosyntacticFeatureBundle'>

`Word.features`: {Aspect: [perfective], Mood: [indicative], Number: [singular], Person: [third], Tense: [past], VerbForm: [finite], Voice: [active]}


In [44]:
creav.features.features.keys()

dict_keys([Aspect, Mood, Number, Person, Tense, VerbForm, Voice])

A user may inspect a `MorphosyntacticFeatureBundle` in a manner similar to a `dict`

In [ ]:
print("Mood:", creav.features["Mood"], creav.features["Mood"][0].name)  # type: List[Mood]
print("Number:", creav.features["Number"])  # type: List[Number]
print("Person:", creav.features["Person"])  # type: List[Person]
print("Tense:", creav.features["Tense"])  # type: List[Tense]
print("VerbForm:", creav.features["VerbForm"])  # type: List[VerbForm]
print("Voice:", creav.features["Voice"])  # type: List[Voice]

# Note: The values returned here are a list, though under normally only one 
# morphological form will be available

Looking a bit closer at `MorphosyntacticFeature`, we can see how its data type inherits from the Python builtin [IntEnu](https://docs.python.org/3/library/enum.html#enum.IntEnum).

In [ ]:
a_mood_obj = a_word_concurrunt.features["Mood"][0]
# see type
print("type(a_mood_obj):", type(a_mood_obj))
print("")
# See inheritance
from enum import IntEnum
print("Is `IntEnum`?", isinstance(a_mood_obj, IntEnum))
print("")
# 
from cltk.morphology.morphosyntax import MorphosyntacticFeature
print("`Mood` inherits from `MorphosyntacticFeature`?", isinstance(a_mood_obj, MorphosyntacticFeature))

In [ ]:
# You can manipulate this object as any IntEnum plus a few extras

print("`MorphosyntacticFeature` accessors:", [x for x in dir(a_mood_obj) if not x.startswith("__")])
print("")
print("MorphosyntacticFeature.name:", a_mood_obj.name)  # type: str
# A stable int value is available, too, associated with this name
print("MorphosyntacticFeature.value:", a_mood_obj.value)  # type: int

Users can create their own `MorphosyntacticFeature` and `MorphosyntacticFeatureBundle`:

In [ ]:
from cltk.morphology.morphosyntax import MorphosyntacticFeatureBundle
from cltk.morphology.universal_dependencies_features import Mood, Number, Person, VerbForm, Voice

latin_word_sim = "sim"

mood = Mood.subjunctive
voice = Voice.active
person = Person.first
number = Number.singular
verb_form = VerbForm.finite

latin_word_sim_bundle = MorphosyntacticFeatureBundle(mood, voice, person, number, verb_form)
print(latin_word_sim_bundle)

Finally, we may even construct a `Word` with this information:

In [ ]:
from cltk.core.data_types import Word

print(Word(string="sim", features=latin_word_sim_bundle))

In [ ]:
# For more on this or any other CLTK class, use `help()`
# help(a_mood_obj)
# help(MorphosyntacticFeatureBundle)

In [ ]:
# Note: Extra morphological info may be written in `str` type
# to to the values at `.upos` and `.xpos` for languages using
# Stanza project

# Note: The particular annoations at these are often inconsistent across
# languages or even treebanks within a single language; hence the benefit
# of the CLTK's modeling at `.pos`.
print("`Word.upos`:", a_word_concurrunt.upos)
print("`Word.xpos`:", a_word_concurrunt.xpos)

## Analyze the whole book of Genesis

In [ ]:
# TODO: get string values of feature names

In [63]:
all_features = set()
all_words = {}

for verse in vulgate_genesis:
    bo, ch, ve = verse
    gen_doc = cltk_nlp.analyze(text=vulgate_genesis[verse])
    for idx, wo in enumerate(gen_doc):
        word_dict = {}
        word_dict['book'] = bo
        word_dict['chapter'] = ch
        word_dict['verse'] = ve
        word_dict['text'] = wo.string
        word_dict['lemma'] = wo.lemma
        word_dict['pos'] = wo.pos
        features = wo.features
        for feat in features.features:
            all_features.add(feat)
            word_dict[feat] = features.features.get(feat)[0]
            
            
        print(word_dict)
        all_words[(bo, ch, ve, idx)] = word_dict
            

{'book': 'Genesis', 'chapter': '1', 'verse': '1', 'text': 'in', 'lemma': 'in', 'pos': adposition, AdpositionalType: preposition}
{'book': 'Genesis', 'chapter': '1', 'verse': '1', 'text': 'principio', 'lemma': 'principium', 'pos': noun, Case: ablative, Gender: neuter, Number: singular}
{'book': 'Genesis', 'chapter': '1', 'verse': '1', 'text': 'creavit', 'lemma': 'creo', 'pos': verb, Aspect: perfective, Mood: indicative, Number: singular, Person: third, Tense: past, VerbForm: finite, Voice: active}
{'book': 'Genesis', 'chapter': '1', 'verse': '1', 'text': 'Deus', 'lemma': 'Deus', 'pos': proper_noun, Case: nominative, Gender: masculine, Number: singular}
{'book': 'Genesis', 'chapter': '1', 'verse': '1', 'text': 'caelum', 'lemma': 'caelum', 'pos': noun, Case: accusative, Gender: neuter, Number: singular}
{'book': 'Genesis', 'chapter': '1', 'verse': '1', 'text': 'et', 'lemma': 'et', 'pos': coordinating_conjunction}
{'book': 'Genesis', 'chapter': '1', 'verse': '1', 'text': 'terram', 'lemma':

{'book': 'Genesis', 'chapter': '1', 'verse': '7', 'text': 'et', 'lemma': 'et', 'pos': coordinating_conjunction}
{'book': 'Genesis', 'chapter': '1', 'verse': '7', 'text': 'fecit', 'lemma': 'facio', 'pos': verb, Aspect: perfective, Mood: indicative, Number: singular, Person: third, Tense: past, VerbForm: finite, Voice: active}
{'book': 'Genesis', 'chapter': '1', 'verse': '7', 'text': 'Deus', 'lemma': 'Deus', 'pos': proper_noun, Case: nominative, Gender: masculine, Number: singular}
{'book': 'Genesis', 'chapter': '1', 'verse': '7', 'text': 'firmamentum', 'lemma': 'firmamentum', 'pos': noun, Case: accusative, Gender: neuter, Number: singular}
{'book': 'Genesis', 'chapter': '1', 'verse': '7', 'text': 'divisitque', 'lemma': 'discio', 'pos': verb, Aspect: perfective, Mood: indicative, Number: plural, Person: third, Tense: past, VerbForm: finite, Voice: active}
{'book': 'Genesis', 'chapter': '1', 'verse': '7', 'text': 'aquas', 'lemma': 'aqua', 'pos': noun, Case: accusative, Gender: feminine, N

{'book': 'Genesis', 'chapter': '1', 'verse': '10', 'text': 'et', 'lemma': 'et', 'pos': coordinating_conjunction}
{'book': 'Genesis', 'chapter': '1', 'verse': '10', 'text': 'vocavit', 'lemma': 'vocavit', 'pos': verb, Aspect: perfective, Mood: indicative, Number: singular, Person: third, Tense: past, VerbForm: finite, Voice: active}
{'book': 'Genesis', 'chapter': '1', 'verse': '10', 'text': 'Deus', 'lemma': 'Deus', 'pos': proper_noun, Case: nominative, Gender: masculine, Number: singular}
{'book': 'Genesis', 'chapter': '1', 'verse': '10', 'text': 'aridam', 'lemma': 'aridus', 'pos': adjective, Case: accusative, Degree: positive, Gender: feminine, Number: singular}
{'book': 'Genesis', 'chapter': '1', 'verse': '10', 'text': 'terram', 'lemma': 'terra', 'pos': noun, Case: accusative, Gender: feminine, Number: singular}
{'book': 'Genesis', 'chapter': '1', 'verse': '10', 'text': 'congregationesque', 'lemma': 'congregatio', 'pos': noun, Case: accusative, Gender: feminine, Number: plural}
{'book'

{'book': 'Genesis', 'chapter': '1', 'verse': '15', 'text': 'ut', 'lemma': 'ut', 'pos': subordinating_conjunction}
{'book': 'Genesis', 'chapter': '1', 'verse': '15', 'text': 'luceant', 'lemma': 'luceo', 'pos': verb, Aspect: imperfective, Mood: subjunctive, Number: plural, Person: third, Tense: present, VerbForm: finite, Voice: active}
{'book': 'Genesis', 'chapter': '1', 'verse': '15', 'text': 'in', 'lemma': 'in', 'pos': adposition, AdpositionalType: preposition}
{'book': 'Genesis', 'chapter': '1', 'verse': '15', 'text': 'firmamento', 'lemma': 'firmamentum', 'pos': noun, Case: ablative, Gender: neuter, Number: singular}
{'book': 'Genesis', 'chapter': '1', 'verse': '15', 'text': 'caeli', 'lemma': 'caelum', 'pos': noun, Case: genitive, Gender: neuter, Number: singular}
{'book': 'Genesis', 'chapter': '1', 'verse': '15', 'text': 'et', 'lemma': 'et', 'pos': coordinating_conjunction}
{'book': 'Genesis', 'chapter': '1', 'verse': '15', 'text': 'inluminent', 'lemma': 'inlumino', 'pos': verb, Aspe

{'book': 'Genesis', 'chapter': '1', 'verse': '21', 'text': 'creavitque', 'lemma': 'creo', 'pos': verb, Aspect: imperfective, Mood: indicative, Number: singular, Person: third, Tense: past, VerbForm: finite, Voice: active}
{'book': 'Genesis', 'chapter': '1', 'verse': '21', 'text': 'Deus', 'lemma': 'Deus', 'pos': proper_noun, Case: nominative, Gender: masculine, Number: singular}
{'book': 'Genesis', 'chapter': '1', 'verse': '21', 'text': 'cete', 'lemma': 'ces', 'pos': noun, Case: accusative, Gender: neuter, Number: plural}
{'book': 'Genesis', 'chapter': '1', 'verse': '21', 'text': 'grandia', 'lemma': 'grandium', 'pos': noun, Case: accusative, Gender: neuter, Number: plural}
{'book': 'Genesis', 'chapter': '1', 'verse': '21', 'text': 'et', 'lemma': 'et', 'pos': coordinating_conjunction}
{'book': 'Genesis', 'chapter': '1', 'verse': '21', 'text': 'omnem', 'lemma': 'omnis', 'pos': determiner, Case: accusative, Gender: feminine, Number: singular, PrononimalType: indefinite}
{'book': 'Genesis',

...

{'book': 'Genesis', 'chapter': '50', 'verse': '8', 'text': 'domus', 'lemma': 'domus', 'pos': noun, Case: nominative, Gender: feminine, Number: singular}
{'book': 'Genesis', 'chapter': '50', 'verse': '8', 'text': 'Ioseph', 'lemma': 'Ioseph', 'pos': proper_noun}
{'book': 'Genesis', 'chapter': '50', 'verse': '8', 'text': 'cum', 'lemma': 'cum', 'pos': adposition, AdpositionalType: preposition}
{'book': 'Genesis', 'chapter': '50', 'verse': '8', 'text': 'fratribus', 'lemma': 'frater', 'pos': noun, Case: ablative, Gender: masculine, Number: plural}
{'book': 'Genesis', 'chapter': '50', 'verse': '8', 'text': 'suis', 'lemma': 'suus', 'pos': determiner, Case: ablative, Gender: masculine, Number: plural, Person: psor, Possessive: pos, PrononimalType: personal, Reflexive: pos}
{'book': 'Genesis', 'chapter': '50', 'verse': '8', 'text': 'absque', 'lemma': 'absque', 'pos': adposition, AdpositionalType: preposition}
{'book': 'Genesis', 'chapter': '50', 'verse': '8', 'text': 'parvulis', 'lemma': 'parvul

{'book': 'Genesis', 'chapter': '50', 'verse': '14', 'text': 'reversusque', 'lemma': 'reversusque', 'pos': verb, Aspect: perfective, Case: nominative, Degree: positive, Gender: masculine, Number: singular, Tense: past, VerbForm: participle, Voice: passive}
{'book': 'Genesis', 'chapter': '50', 'verse': '14', 'text': 'est', 'lemma': 'sum', 'pos': auxiliary, Mood: indicative, Number: singular, Person: third, Tense: present, VerbForm: finite, Voice: active}
{'book': 'Genesis', 'chapter': '50', 'verse': '14', 'text': 'Ioseph', 'lemma': 'Ioseph', 'pos': proper_noun}
{'book': 'Genesis', 'chapter': '50', 'verse': '14', 'text': 'in', 'lemma': 'in', 'pos': adposition, AdpositionalType: preposition}
{'book': 'Genesis', 'chapter': '50', 'verse': '14', 'text': 'Aegyptum', 'lemma': 'Aegyptum', 'pos': noun, Case: accusative, Gender: masculine, Number: singular}
{'book': 'Genesis', 'chapter': '50', 'verse': '14', 'text': 'cum', 'lemma': 'cum', 'pos': adposition, AdpositionalType: preposition}
{'book': 

{'book': 'Genesis', 'chapter': '50', 'verse': '17', 'text': 'ut', 'lemma': 'ut', 'pos': subordinating_conjunction}
{'book': 'Genesis', 'chapter': '50', 'verse': '17', 'text': 'haec', 'lemma': 'hic', 'pos': pronoun, Case: accusative, Gender: neuter, Number: plural, PrononimalType: demonstrative}
{'book': 'Genesis', 'chapter': '50', 'verse': '17', 'text': 'tibi', 'lemma': 'tu', 'pos': pronoun, Case: dative, Gender: masculine, Number: singular, PrononimalType: personal}
{'book': 'Genesis', 'chapter': '50', 'verse': '17', 'text': 'verbis', 'lemma': 'verbis', 'pos': noun, Case: dative, Gender: masculine, Number: plural}
{'book': 'Genesis', 'chapter': '50', 'verse': '17', 'text': 'illius', 'lemma': 'ille', 'pos': pronoun, Case: genitive, Gender: masculine, Number: singular, PrononimalType: demonstrative}
{'book': 'Genesis', 'chapter': '50', 'verse': '17', 'text': 'diceremus', 'lemma': 'dico', 'pos': verb, Aspect: imperfective, Mood: subjunctive, Number: plural, Person: first, Tense: past, Ve

{'book': 'Genesis', 'chapter': '50', 'verse': '20', 'text': 'vos', 'lemma': 'vos', 'pos': pronoun, Case: nominative, Gender: masculine, Number: plural, PrononimalType: personal}
{'book': 'Genesis', 'chapter': '50', 'verse': '20', 'text': 'cogitastis', 'lemma': 'cogito', 'pos': verb, Aspect: perfective, Mood: indicative, Number: plural, Person: second, Tense: past, VerbForm: finite, Voice: active}
{'book': 'Genesis', 'chapter': '50', 'verse': '20', 'text': 'de', 'lemma': 'de', 'pos': adposition, AdpositionalType: preposition}
{'book': 'Genesis', 'chapter': '50', 'verse': '20', 'text': 'me', 'lemma': 'ego', 'pos': pronoun, Case: ablative, Gender: masculine, Number: singular, PrononimalType: personal}
{'book': 'Genesis', 'chapter': '50', 'verse': '20', 'text': 'malum', 'lemma': 'malum', 'pos': noun, Case: accusative, Gender: neuter, Number: singular}
{'book': 'Genesis', 'chapter': '50', 'verse': '20', 'text': 'et', 'lemma': 'et', 'pos': coordinating_conjunction}
{'book': 'Genesis', 'chapt

{'book': 'Genesis', 'chapter': '50', 'verse': '24', 'text': 'cumque', 'lemma': 'cumque', 'pos': subordinating_conjunction}
{'book': 'Genesis', 'chapter': '50', 'verse': '24', 'text': 'adiurasset', 'lemma': 'adiuro', 'pos': verb, Aspect: perfective, Mood: subjunctive, Number: singular, Person: third, Tense: pluperfect, VerbForm: finite, Voice: active}
{'book': 'Genesis', 'chapter': '50', 'verse': '24', 'text': 'eos', 'lemma': 'is', 'pos': pronoun, Case: accusative, Gender: masculine, Number: plural, PrononimalType: demonstrative}
{'book': 'Genesis', 'chapter': '50', 'verse': '24', 'text': 'atque', 'lemma': 'atque', 'pos': coordinating_conjunction}
{'book': 'Genesis', 'chapter': '50', 'verse': '24', 'text': 'dixisset', 'lemma': 'dico', 'pos': verb, Aspect: perfective, Mood: subjunctive, Number: singular, Person: third, Tense: pluperfect, VerbForm: finite, Voice: active}
{'book': 'Genesis', 'chapter': '50', 'verse': '24', 'text': 'Deus', 'lemma': 'Deus', 'pos': proper_noun, Case: nominati

In [64]:
features_genesis = {}

all_features = list(all_features)

for key in all_words:
    w_dict = all_words[key]
    feature_list = [w_dict['book'], w_dict['chapter'], w_dict['verse'], w_dict['text'], w_dict['lemma'], w_dict['pos']]
    for feature in all_features:
        feature_value = w_dict.get(feature, '-')
        feature_list.append(feature_value)
    features_genesis[key] = feature_list

In [75]:
all_features


[Numeral,
 NumForm,
 Number,
 Voice,
 PrononimalType,
 Tense,
 Reflexive,
 Polarity,
 Gender,
 Abbreviation,
 Case,
 Aspect,
 VerbType,
 AdpositionalType,
 Mood,
 Possessive,
 Person,
 VerbForm,
 Degree]

In [66]:
genesis = pd.DataFrame(features_genesis).T

In [72]:
genesis_colnames = ['book', 'chapter','verse', 'text', 'lemma', 'pos'] + all_features
genesis.columns = genesis_colnames

['book',
 'chapter',
 'verse',
 'text',
 'lemma',
 'pos',
 Numeral,
 NumForm,
 Number,
 Voice,
 PrononimalType,
 Tense,
 Reflexive,
 Polarity,
 Gender,
 Abbreviation,
 Case,
 Aspect,
 VerbType,
 AdpositionalType,
 Mood,
 Possessive,
 Person,
 VerbForm,
 Degree]

In [68]:
genesis.shape

(26758, 25)

In [74]:
genesis.head()

book chapter verse       text       lemma          pos  \
Genesis 1 1 0  Genesis       1     1         in          in   adposition   
            1  Genesis       1     1  principio  principium         noun   
            2  Genesis       1     1    creavit        creo         verb   
            3  Genesis       1     1       Deus        Deus  proper_noun   
            4  Genesis       1     1     caelum      caelum         noun   

              (cardinal, distributive, fractional, multiplicative, ordinal, range, sets)  \
Genesis 1 1 0                                                  -                           
            1                                                  -                           
            2                                                  -                           
            3                                                  -                           
            4                                                  -                           

              (word, digit, roman, reference)  \
Genesis 1 1 0                               -   
            1                               -   
            2                               -   
            3                               -   
            4                               -   

              (collective, count_plural, dual, greater_paucal, greater_plural, inverse_number, paucal, plural, plurale_tantum, singular, trial, psor)  \
Genesis 1 1 0                                                  -                                                                                        
            1                                           singular                                                                                        
            2                                           singular                                                                                        
            3                                           singular                                                                                        
            4                                           singular                                                                                        

              (active, antipassive, beneficiary_focus, location_focus, causative, direct, inverse, middle, passive, reciprocal)  \
Genesis 1 1 0                                                  -                                                                  
            1                                                  -                                                                  
            2                                             active                                                                  
            3                                                  -                                                                  
            4                                                  -                                                                  

               ... (pos, neg)  \
Genesis 1 1 0  ...          -   
            1  ...          -   
            2  ...          -   
            3  ...          -   
            4  ...          -   

              (nominative, accusative, ergative, absolutive, abessive, befefactive, causative, comparative, considerative, comitative, dative, distributive, equative, genitive, instrumental, partitive, vocative, ablative, additive, adessive, allative, delative, elative, essive, illative, inessive, lative, locative, perlative, sublative, superessive, terminative, temporal, translative)  \
Genesis 1 1 0                                                  -                                                                                                                                                                                                                                                                                                                                      
            1             

In [70]:
genesis.to_csv('genesis.csv', index=False)

# Modeling syntax with `Form` and `DependencyTree`  <a name="syntax"></a>

The CLTK uses the builtin `xml` library to build tree for modeling dependency parses. A `Word` is mapped into a `Form`, then `ElemntTree` is used to organize these `Form`s into a `DependencyTree`. With a tree, certain measurements are more efficient (counting depth, breadth, edge types).

In [ ]:
from cltk.dependency.tree import DependencyTree

In [ ]:
# Let's look at this sentence again
print(cltk_doc.sentences_strings[6])  # text form of `sentence_6`

In [ ]:
a_tree = DependencyTree.to_tree(sentence_6)

In [ ]:
from pprint import pprint

pprint(a_tree.get_dependencies())

In [ ]:
a_tree.print_tree()

# Feature extraction <a name="features"></a>

The CLTK offers the function `cltk_doc_to_features_table()`, which assist users when preparing a `Doc` for training data for machine learning. It converts the list of `Word` objects at `Doc.words` into a tabular list of lists.

In [ ]:
from cltk.utils.feature_extraction import cltk_doc_to_features_table

In [ ]:
feature_names, list_of_list_features = cltk_doc_to_features_table(cltk_doc=cltk_doc)

In [ ]:
# See here the names of the features extracted
print(feature_names)

In [ ]:
# Number of "inner lists" matches number of tokens
print("Number tokens:", len(cltk_doc.words))
print("len() of feature instances (one for each token):", len(list_of_list_features))

In [ ]:
# Look at one row of data `(variable name, variable value)`
pprint(list(zip(feature_names, list_of_list_features[108])))

# Brief demonstration of `NLP()` for Ancient Greek <a name="greek-nlp"></a>

The API for Greek is the same as Latin.

In [ ]:
# read the Ancient Greek file
with open("grc-thucydides.txt") as fo:
    thucydides_full = fo.read()

In [ ]:
print("Text snippet:", thucydides_full[0:200])
print("Character count:", len(thucydides_full))
print("Approximate token count:", len(thucydides_full.split()))

In [ ]:
len(thucydides_full) // 7

In [ ]:
# Cut this down to roughly 10k tokens for this demonstration's purposes
thucydides = thucydides_full[:len(thucydides_full) // 7]
print("Approximate token count:", len(thucydides.split()))

In [ ]:
thucydides[:200]

In [ ]:
cltk_nlp_grc = NLP(language="grc")

In [ ]:
# Execution time is 50 sec on a 2015 Macbook Pro
%time cltk_doc_grc = cltk_nlp_grc.analyze(text=thucydides)

# You will be asked to download some models (from CLTK, fastText, and Stanza)

In [ ]:
print("`Doc.tokens`:", cltk_doc_grc.tokens[:20])

In [ ]:
print(cltk_doc_grc.words[4])  # πόλεμον ('war')

In [ ]:
a_tree_grc = DependencyTree.to_tree(cltk_doc_grc.sentences[0])  #81

In [ ]:
pprint(a_tree_grc.get_dependencies())

In [ ]:
print(cltk_doc_grc.sentences_strings[0])
print("")
print("Translation:", "Thucydides, an Athenian, wrote the history of the war between the Peloponnesians and the Athenians, beginning at the moment that it broke out, and believing that it would be a great war, and more worthy of relation than any that had preceded it. This belief was not without its grounds. The preparations of both the combatants were in every department in the last state of perfection; and he could see the rest of the Hellenic race taking sides in the quarrel; those who delayed doing so at once having it in contemplation.")
print("")
a_tree_grc.print_tree()

In [ ]:
feature_names_grc, list_of_list_features_grc = cltk_doc_to_features_table(cltk_doc=cltk_doc_grc)

In [ ]:
print(feature_names_grc)

In [ ]:
print("len() of feature instances (one for each token):", len(list_of_list_features_grc))
print("")
print("Example of one instance row:", list_of_list_features_grc[4])

In [ ]:
# Putting these together for easier reading
pprint(list(zip(feature_names_grc, list_of_list_features_grc[4])))